# Heatmap(s) in (geo) maps of the Netherlands using bokeh
## (levels: postcode, gemeente, and provinces)

In [193]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline
# import seaborn as sns
# plt.style.use('fivethirtyeight')

import json
from collections import OrderedDict

# https://bokeh.pydata.org
from bokeh.io import output_notebook, export_svgs
from bokeh.plotting import figure, show
from bokeh.models import (GeoJSONDataSource,ColumnDataSource,HoverTool,LogColorMapper,ColorBar,LogTicker)
output_notebook()

Loading BokehJS ...

## Loading .kml and .geojson of the Netherlands

In [157]:
# Found at: https://www.webuildinternet.com/2015/06/18/map-polygons-for-the-netherlands/
# CONVERTED from kml to geojson:
#    !ogr2ogr -f GeoJSON Polygonen_NL_Postcodes_4PP.geojson Polygonen\ NL\ Postcodes\ 4PP.kml
with open(r'Polygonen_NL_Postcodes_4PP.geojson', 'r') as f:
    nl_postcodes = json.loads(f.read(), object_hook=OrderedDict)

# FOUND at: https://www.webuildinternet.com/2015/07/09/geojson-data-of-the-netherlands/
with open(r'provinces.geojson', 'r') as f:
    nl_provinces = json.loads(f.read(), object_hook=OrderedDict)

# FOUND at: https://www.webuildinternet.com/2015/07/09/geojson-data-of-the-netherlands/    
with open(r'townships.geojson', 'r') as f:
    nl_gemeentes = json.loads(f.read(), object_hook=OrderedDict)


## Plotting the NL postcodes

In [158]:
geo_source = GeoJSONDataSource(geojson=json.dumps(nl_postcodes))

In [159]:
# nl_postcodes['features'][0]['properties']['Description'].split('</b> ')[1].replace(' </div>','')

In [162]:
palette.reverse()
color_mapper = LogColorMapper(palette=palette)

TOOLS = "pan,wheel_zoom,box_zoom,reset,hover,save"

p = figure(
    title="Netherlands Postcodes", 
    tools=TOOLS,
     x_axis_location=None, y_axis_location=None
)

p.patches('xs', 'ys', source=geo_source,
#           fill_color={'field': 'AverageIncome', 
#                       'transform': color_mapper},
          fill_alpha=0.7, line_color="black", line_width=0.5)

hover = p.select_one(HoverTool)
hover.point_policy = "follow_mouse"
hover.tooltips = [
    ("Postcode", "@Description"),
]

p.grid.grid_line_color = None
p.background_fill_color = None
p.border_fill_color = None
p.output_backend = "svg"

show(p)

##  Plotting the NL Gemeentes

In [164]:
geo_source = GeoJSONDataSource(geojson=json.dumps(nl_gemeentes))

In [165]:
palette.reverse()
color_mapper = LogColorMapper(palette=palette)

TOOLS = "pan,wheel_zoom,box_zoom,reset,hover,save"

p = figure(
    title="Netherlands Gemeentes", 
    tools=TOOLS,
     x_axis_location=None, y_axis_location=None
)

p.patches('xs', 'ys', source=geo_source,
          fill_alpha=0.7, line_color="black", line_width=0.5)

hover = p.select_one(HoverTool)
hover.point_policy = "follow_mouse"
hover.tooltips = [
    ("Name", "@name")]

p.grid.grid_line_color = None
p.background_fill_color = None
p.border_fill_color = None
p.output_backend = "svg"

show(p)

## Plotting NL Provinces 

In [167]:
geo_source = GeoJSONDataSource(geojson=json.dumps(nl_provinces))

In [168]:
palette.reverse()
color_mapper = LogColorMapper(palette=palette)

TOOLS = "pan,wheel_zoom,box_zoom,reset,hover,save"

p = figure(
    title="Netherlands Provinces", 
    tools=TOOLS,
     x_axis_location=None, y_axis_location=None
)

p.patches('xs', 'ys', source=geo_source,
          fill_alpha=0.7, line_color="black", line_width=0.5)

hover = p.select_one(HoverTool)
hover.point_policy = "follow_mouse"
hover.tooltips = [
    ("Name", "@name")
]

p.grid.grid_line_color = None
p.background_fill_color = None
p.border_fill_color = None
p.output_backend = "svg"

show(p)

# HOW TO MANIPULATE THOSE GRAPHS FOR A HEAT MAP

## Let's take a look on the information they have

In [169]:
display(nl_postcodes['features'][0]['properties'])

display(nl_provinces['features'][0]['properties'])

display(nl_gemeentes['features'][0]['properties'])

OrderedDict([('Name', ''),
             ('Description',
              '<div class="googft-info-window"> <b>PC4CODE:</b> 3566 </div>')])

OrderedDict([('name', 'Drenthe'),
             ('regioFacetId', 'tcm:106-353397-1024'),
             ('level', 3)])

OrderedDict([('code', '1680'),
             ('name', 'Aa en Hunze'),
             ('regioFacet', 'tcm:106-353398-1024'),
             ('level', 4),
             ('url', '/regioinformatie/gemeente/aa-en-hunze/')])

## Let's list the provinces

In [170]:
for province in nl_provinces['features']:
    print(province['properties']['name'])

Drenthe
Flevoland
Friesland (Fryslân)
Gelderland
Groningen
Limburg
Noord-Brabant
Noord-Holland
Overijssel
Utrecht
Zeeland
Zuid-Holland


## Let's create random numbers to each province

In [184]:
import random

df_provinces_stats = pd.DataFrame([])

for province in nl_provinces['features']:  
    province_name = province['properties']['name']
    df_provinces_stats = df_provinces_stats.append(pd.DataFrame({'province': province_name,
                               'value':random.uniform(1,100)}, index=[0]), ignore_index=True)


## Now, we must to MERGE the 'created'  data with the geojson  

In [185]:
missing=[]
for province in nl_provinces['features']: 
    province_name = province['properties']['name']
    try:
        value = df_provinces_stats[df_provinces_stats['province']==province_name]['value'].values[0]
    except:
        value = 0
        missing.append(province_name)
        
    province['properties']['created_values'] = value

## Check whether the geojson was updated

In [186]:
for province in nl_provinces['features']:
    print (province['properties']['name'], province['properties']['created_values'])

Drenthe 28.431749810080117
Flevoland 6.045965376734359
Friesland (Fryslân) 34.20523039099646
Gelderland 95.91359738175512
Groningen 23.663318741840495
Limburg 25.8840128424383
Noord-Brabant 52.979050740564965
Noord-Holland 60.530671967707036
Overijssel 29.327089896280665
Utrecht 99.67571299982775
Zeeland 30.59204005051002
Zuid-Holland 31.0413960972025


## Plotting the heatmap

In [187]:
geo_source = GeoJSONDataSource(geojson=json.dumps(nl_provinces))

In [214]:
from bokeh.palettes import Oranges9 as palette # https://bokeh.pydata.org/en/latest/docs/reference/palettes.html
palette.reverse() #for heatmap 
color_mapper = LogColorMapper(palette=palette,low=1,high=100)


TOOLS = "pan,wheel_zoom,box_zoom,reset,hover,save"

p = figure(
    title="Random numbers related to Dutch provinces", 
    tools=TOOLS,
     x_axis_location=None, y_axis_location=None
)

p.patches('xs', 'ys', 
          source=geo_source,
          fill_color={'field': 'created_values', 
                      'transform': color_mapper},
          fill_alpha=1, 
          line_color="black", 
          line_width=0.5)


hover = p.select_one(HoverTool)
hover.point_policy = "follow_mouse"
hover.tooltips = [
    ("Name", "@name"),
    ("Created Values", "@created_values"),
]

color_bar = ColorBar(color_mapper=color_mapper, 
                     ticker=LogTicker(),
                     label_standoff=5, 
                     border_line_color=None, 
                     location=(0,0))
p.add_layout(color_bar, 'right')

p.grid.grid_line_color = None
p.background_fill_color = None
p.border_fill_color = None
p.output_backend = "svg"


show(p)